# Preliminary settings

Libraries imported.

In [12]:
import os
import re
import json
import pickle
import numpy as np
import matplotlib.pyplot as plt

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.applications import efficientnet
from tensorflow.keras.layers import TextVectorization

Set a randomizer.

In [13]:
from datetime import datetime
seed = int(round(datetime.now().timestamp()))
np.random.seed(seed)
tf.random.set_seed(seed)

Important constants.

In [14]:
# Desired image dimensions
IMAGE_SIZE = (299, 299)

# Vocabulary size
VOCAB_SIZE = 6000

# Fixed length allowed for any sequence
SEQ_LENGTH = 8

# Dimension for the image embeddings and token embeddings
EMBED_DIM = 256

# Per-layer units in the feed-forward network
FF_DIM = 256

# Setting parameters of the model

Set the version of the model and the path to the vocabulary of vectorised captions.

In [15]:
mdx = '231005'
dxx = f'/data/Vocab/{mdx}/'

Load the vocabulary.

In [16]:
filepath = f'{dxx}vocab_{mdx}'
try:
    print(f"Loading vocabulary from {filepath}")
    with open(filepath, "rb") as f:
        vx = pickle.load(f)
    print("Vocabulary loaded successfully")
        
    global VOCAB_SIZE
    VOCAB_SIZE = len(vx)
except Exception as e:
    print(f"Error loading vocabulary file: {e}")

Loading vocabulary from /data/Vocab/231005/vocab_231005
Vocabulary loaded successfully


Set the image augmentation and vectorisation functions to be used in the model.

In [17]:
def custom_standardization(input_string):
    lowercase = tf.strings.lower(input_string)
    return tf.strings.regex_replace(lowercase, "[%s]" % re.escape(strip_chars), "")


# Using raw string for strip_chars
strip_chars = r"!\"#$%&'()*+,-./:;<=>?@[\]^_`{|}~"
strip_chars = strip_chars.replace("<", "").replace(">", "")

# Initialize TextVectorization
try:
    if vx:
        vectorization = TextVectorization(
            max_tokens=VOCAB_SIZE,
            output_mode="int",
            output_sequence_length=SEQ_LENGTH,
            standardize=custom_standardization,
            vocabulary=vx,
        )
    else:
        raise ValueError("Vocabulary is not defined.")
except Exception as e:
    print(f"Error initializing TextVectorization: {e}")
    vectorization = None


# Data augmentation for image data
image_augmentation = keras.Sequential(
    [
        layers.RandomFlip("horizontal"),
        layers.RandomRotation(0.1), # Reduced rotation for faster preprocessing
        layers.RandomContrast(0.2), # Lighter contrast adjustment
        # layers.RandomTranslation(0.1, 0.1),
    ]
)

Image loading and decoding function.

In [18]:
# Decode, resize, and preprocess images
def decode_and_resize(img_path):
    try:
        img = tf.io.read_file(img_path)
        img = tf.image.decode_jpeg(img, channels=3)
        img = tf.image.resize(img, IMAGE_SIZE)
        img = tf.image.convert_image_dtype(img, tf.float32)
        return img
    except Exception as e:
        print(f"Error in decoding and resizing image {img_path}: {e}")

# Transformer model

Create the same Transformer model as used in training.

In [19]:
# Defining the Model
# CNN
def get_cnn_model():
    try:
        base_model = efficientnet.EfficientNetB0(
            input_shape=(*IMAGE_SIZE, 3),
            include_top=False,
            weights="imagenet",
        )
        # We freeze our feature extractor
        base_model.trainable = False
        base_model_out = base_model.output
        
        # Reduce the sequence length using a pooling operation
        # Using GlobalAveragePooling2D to reduce the spatial dimensions
        base_model_out = layers.GlobalAveragePooling2D()(base_model_out)
        
        # Project the output to match the embedding size
        base_model_out = layers.Dense(EMBED_DIM)(base_model_out)
        
        cnn_model = keras.models.Model(base_model.input, base_model_out)
        
        # Print CNN Model Summary
        print("\nCNN Model Summary:")
        cnn_model.summary()
        
        return cnn_model
    except Exception as e:
        print(f"Error loading CNN model: {e}")


# Positional Encoding and Encoder/Decoder

# Encoder
class TransformerEncoderBlock(layers.Layer):
    def __init__(self, embed_dim, dense_dim, num_heads, **kwargs):
        super().__init__(**kwargs)
        self.embed_dim = embed_dim
        self.dense_dim = dense_dim
        self.num_heads = num_heads
        self.attention_1 = layers.MultiHeadAttention(
            num_heads=num_heads, key_dim=embed_dim, dropout=0.0 # previously 0.1
        )
        self.layernorm_1 = layers.LayerNormalization()
        self.layernorm_2 = layers.LayerNormalization()
        self.dense_1 = layers.Dense(embed_dim, activation="relu")

    def call(self, inputs, training, mask=None):
        # Input shape
        print(f"Encoder Input Shape: {inputs.shape}")

        print(f"Encoder Input Shape before LayerNorm: {inputs.shape}")
        inputs = self.layernorm_1(inputs)
        print(f"Encoder Input Shape after LayerNorm: {inputs.shape}")
        
        inputs = self.dense_1(inputs)

        attention_output_1 = self.attention_1(
            query=inputs,
            value=inputs,
            key=inputs,
            attention_mask=None,
            training=training,
        )
        
        out_1 = self.layernorm_2(inputs + attention_output_1)

        # Output shape
        print(f"Encoder Output Shape: {out_1.shape}")
        return out_1


# Positional Encoding
class PositionalEmbedding(layers.Layer):
    def __init__(self, sequence_length, vocab_size, embed_dim, **kwargs):
        super().__init__(**kwargs)
        self.token_embeddings = layers.Embedding(
            input_dim=vocab_size, output_dim=embed_dim
        )
        self.position_embeddings = layers.Embedding(
            input_dim=sequence_length, output_dim=embed_dim
        )
        self.sequence_length = sequence_length
        self.vocab_size = vocab_size
        self.embed_dim = embed_dim
        self.embed_scale = tf.math.sqrt(tf.cast(embed_dim, tf.float32))

    def call(self, inputs):
        print(f"Positional Embedding Input Shape: {inputs.shape}")
        
        # Get input shape and positions
        length = tf.shape(inputs)[-1]
        positions = tf.range(start=0, limit=length, delta=1)
        
        # Embed tokens and positions
        embedded_tokens = self.token_embeddings(inputs)
        embedded_tokens = embedded_tokens * self.embed_scale # Apply scaling
        embedded_positions = self.position_embeddings(positions)
        
        # Embeddings shape
        print(f"Positional Embedding Output Shape: {embedded_tokens.shape}")
        print(f"embedded_tokens dtype: {embedded_tokens.dtype}")
        print(f"embedded_positions dtype: {embedded_positions.dtype}")
        
        # Return combined embeddings
        return embedded_tokens + embedded_positions

    def compute_mask(self, inputs, mask=None):
        return tf.math.not_equal(inputs, 0)


# Decoder
class TransformerDecoderBlock(layers.Layer):
    def __init__(self, embed_dim, ff_dim, num_heads, **kwargs):
        super().__init__(**kwargs)
        self.embed_dim = embed_dim
        self.ff_dim = ff_dim
        self.num_heads = num_heads
        
        # Attention layers
        self.attention_1 = layers.MultiHeadAttention(
            num_heads=num_heads, key_dim=embed_dim, dropout=0.1
        )
        self.attention_2 = layers.MultiHeadAttention(
            num_heads=num_heads, key_dim=embed_dim, dropout=0.1
        )

        # Feed-forward layers
        self.ffn_layer_1 = layers.Dense(ff_dim, activation="relu")
        self.ffn_layer_2 = layers.Dense(embed_dim)

        # Layer normalizations
        self.layernorm_1 = layers.LayerNormalization()
        self.layernorm_2 = layers.LayerNormalization()
        self.layernorm_3 = layers.LayerNormalization()

        # Output layers
        self.embedding = PositionalEmbedding(
            embed_dim=EMBED_DIM, sequence_length=SEQ_LENGTH, vocab_size=VOCAB_SIZE
        )
        self.out = layers.Dense(VOCAB_SIZE, activation="softmax")

        # Dropout layers
        self.dropout_1 = layers.Dropout(0.3) # previously 0.1
        self.dropout_2 = layers.Dropout(0.5) # previously 0.1
        self.supports_masking = True

    def call(self, inputs, encoder_outputs, training, mask=None):
        """
        Args:
            inputs: Tokenized inputs to the decoder (batch_size, sequence_length).
            encoder_outputs: Outputs from the encoder (batch_size, seq_len, embed_dim).
            training: Boolean indicating whether it's training or inference.
            mask: Mask for padded tokens (batch_size, sequence_length).
        
        Returns:
            preds: Decoder output predictions (batch_size, seq_len, vocab_size).
        """
        print(f"Decoder Input Shape: {inputs.shape}")
        
        inputs = self.embedding(inputs)
        causal_mask = self.get_causal_attention_mask(inputs)

        if mask is not None:
            padding_mask = tf.cast(mask[:, :, tf.newaxis], dtype=tf.int32)
            combined_mask = tf.cast(mask[:, tf.newaxis, :], dtype=tf.int32)
            combined_mask = tf.minimum(combined_mask, causal_mask)

        # Self-attention
        attention_output_1 = self.attention_1(
            query=inputs,
            value=inputs,
            key=inputs,
            attention_mask=combined_mask,
            training=training,
        )
        out_1 = self.layernorm_1(inputs + attention_output_1)

        # Cross-attention with encoder outputs
        attention_output_2 = self.attention_2(
            query=out_1,
            value=encoder_outputs,
            key=encoder_outputs,
            attention_mask=padding_mask,
            training=training,
        )
        out_2 = self.layernorm_2(out_1 + attention_output_2)

        # Feed-forward network
        ffn_out = self.ffn_layer_1(out_2)
        ffn_out = self.dropout_1(ffn_out, training=training)
        ffn_out = self.ffn_layer_2(ffn_out)

        ffn_out = self.layernorm_3(ffn_out + out_2, training=training)
        ffn_out = self.dropout_2(ffn_out, training=training)
        preds = self.out(ffn_out)
        
        print(f"Decoder Output Shape: {preds.shape}")
        return preds

    def get_causal_attention_mask(self, inputs):
        input_shape = tf.shape(inputs)
        batch_size, sequence_length = input_shape[0], input_shape[1]
        i = tf.range(sequence_length)[:, tf.newaxis]
        j = tf.range(sequence_length)
        mask = tf.cast(i >= j, dtype="int32")
        mask = tf.reshape(mask, (1, input_shape[1], input_shape[1]))
        mult = tf.concat(
            [tf.expand_dims(batch_size, -1), tf.constant([1, 1], dtype=tf.int32)],
            axis=0,
        )
        return tf.tile(mask, mult)


# Model definition
class ImageCaptioningModel(keras.Model):
    def __init__(
        self, cnn_model, encoder, decoder, num_captions_per_image=2, image_aug=None,
    ):
        super().__init__()
        self.cnn_model = cnn_model
        self.encoder = encoder
        self.decoder = decoder
        self.loss_tracker = keras.metrics.Mean(name="loss")
        self.acc_tracker = keras.metrics.Mean(name="accuracy")
        self.num_captions_per_image = num_captions_per_image
        self.image_aug = image_aug

    def calculate_loss(self, y_true, y_pred, mask):
        loss = self.loss(y_true, y_pred)
        mask = tf.cast(mask, dtype=loss.dtype)
        loss *= mask
        return tf.reduce_sum(loss) / tf.reduce_sum(mask)

    def calculate_accuracy(self, y_true, y_pred, mask):
        accuracy = tf.equal(y_true, tf.argmax(y_pred, axis=2))
        accuracy = tf.math.logical_and(mask, accuracy)
        accuracy = tf.cast(accuracy, dtype=tf.float32)
        mask = tf.cast(mask, dtype=tf.float32)
        return tf.reduce_sum(accuracy) / tf.reduce_sum(mask)

    def _compute_caption_loss_and_acc(self, img_embed, batch_seq, training=True):
        print(f"Image Embedding Input Shape before passing to Encoder: {img_embed.shape}")
        
        # batch_seq = tf.expand_dims(batch_seq, axis=1)
        print(f"Batch Sequence Input Shape before slicing: {batch_seq.shape}")
        
        encoder_out = self.encoder(img_embed, training=training)
        batch_seq_inp = batch_seq[:, :-1] # Input sequence (without the last token)

        print(f"Batch Sequence Input Shape before target sequence: {batch_seq_inp.shape}")
        
        batch_seq_true = batch_seq[:, 1:] # Target sequence (without the first token)
        mask = tf.math.not_equal(batch_seq_true, 0)
        
        print(f"Batch Sequence Input Shape: {batch_seq_inp.shape}")
        print(f"Batch Sequence True Shape: {batch_seq_true.shape}")
        
        batch_seq_pred = self.decoder(
            batch_seq_inp, encoder_out, training=training, mask=mask
        )

        print(f"Batch Sequence Predicted Shape: {batch_seq_pred.shape}")
        
        loss = self.calculate_loss(batch_seq_true, batch_seq_pred, mask)
        acc = self.calculate_accuracy(batch_seq_true, batch_seq_pred, mask)
        return loss, acc

    def train_step(self, batch_data):
        batch_img, batch_seq = batch_data

        # batch_seq = tf.expand_dims(batch_seq, axis=1)

        print(f"Training Image Batch Shape before passing to CNN: {batch_img.shape}")
        total_loss = 0
        total_acc = 0
    
        if self.image_aug:
            batch_img = self.image_aug(batch_img)

        print(f"Training Image Batch Shape: {batch_img.shape}")
        print(f"Training Sequence Batch Shape: {batch_seq.shape}")
        
        # 1. Get image embeddings from CNN
        img_embed = self.cnn_model(batch_img)
        print(f"Image Embeddings Shape: {img_embed.shape}")

        # 2. Reshape CNN output to (batch_size, 1, embedding_dim)
        img_embed = tf.expand_dims(img_embed, axis=1)  # It should be (None, 1, 1024)

        print(f"Reshaped Image Embeddings for Encoder: {img_embed.shape}")
        
        # 3. Make sure batch_seq has 3 dimensions
        if batch_seq.shape.ndims == 2:
            # Reshape the sequence to have a third dimension (e.g., 1 caption per image)
            batch_seq = tf.expand_dims(batch_seq, axis=1)
        
        print(f"Updated Sequence Shape: {batch_seq.shape}")

        # 4. Accumulate loss and accuracy for each caption
        with tf.GradientTape() as tape:
            # Loop through each caption (batch_seq should be (batch_size, num_captions, sequence_length))
            num_captions_per_image = batch_seq.shape[1] # Extract the num_captions dimension
            
            for i in range(self.num_captions_per_image):
                loss, acc = self._compute_caption_loss_and_acc(
                    img_embed, batch_seq[:, i, :], training=True
                )
                total_loss += loss
                total_acc += acc

            # 5. Compute the mean loss and accuracy
            avg_loss = total_loss / tf.cast(self.num_captions_per_image, dtype=tf.float32)
            avg_acc = total_acc / tf.cast(self.num_captions_per_image, dtype=tf.float32)

        # Backpropagation
        # 6. Get the list of all the trainable weights
        train_vars = self.encoder.trainable_variables + self.decoder.trainable_variables
        
        # 7. Get the gradients (from the accumulated loss)
        grads = tape.gradient(avg_loss, train_vars)
    
        # 8. Update the trainable weights
        self.optimizer.apply_gradients(zip(grads, train_vars))
    
        # 9. Update the trackers
        self.loss_tracker.update_state(avg_loss)
        self.acc_tracker.update_state(avg_acc)
    
        # 10. Return the loss and accuracy values
        return {"loss": self.loss_tracker.result(), "acc": self.acc_tracker.result()}

    def test_step(self, batch_data):
        batch_img, batch_seq = batch_data
        print(f"Validation Image Batch Shape: {batch_img.shape}")
        print(f"Validation Sequence Batch Shape: {batch_seq.shape}")

        # batch_seq = tf.expand_dims(batch_seq, axis=1)

        batch_loss = 0
        batch_acc = 0

        # 1. Get image embeddings
        img_embed = self.cnn_model(batch_img)
        print(f"Image Embeddings Shape: {img_embed.shape}")
        img_embed = tf.expand_dims(img_embed, axis=1)
        print(f"Reshaped Image Embeddings Shape: {img_embed.shape}")

        # 2. Pass each of the captions one by one to the decoder
        # along with the encoder outputs and compute the loss as well as accuracy
        # for each caption.
        # Loop through captions
        for i in range(self.num_captions_per_image):
            batch_seq_inp = batch_seq[:, i, :-1]
            batch_seq_true = batch_seq[:, i, 1:]
            print(f"Validation Sequence Input Shape: {batch_seq_inp.shape}")
            print(f"Validation Sequence True Shape: {batch_seq_true.shape}")
        
            loss, acc = self._compute_caption_loss_and_acc(
                img_embed, batch_seq[:, i, :], training=False
            )

            # 3. Update batch loss and batch accuracy
            batch_loss += loss
            batch_acc += acc

        batch_acc /= float(self.num_captions_per_image)

        # 4. Update the trackers
        self.loss_tracker.update_state(batch_loss)
        self.acc_tracker.update_state(batch_acc)

        # 5. Return the loss and accuracy values
        return {"loss": self.loss_tracker.result(), "acc": self.acc_tracker.result()}

    @property
    def metrics(self):
        # We need to list our metrics here so the `reset_states()` can be
        # called automatically.
        return [self.loss_tracker, self.acc_tracker]

# Model construction

# Initialize components
cnn_model = get_cnn_model()
encoder = TransformerEncoderBlock(embed_dim=EMBED_DIM, dense_dim=FF_DIM, num_heads=1)
decoder = TransformerDecoderBlock(embed_dim=EMBED_DIM, ff_dim=FF_DIM, num_heads=2)


CNN Model Summary:
Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            [(None, 299, 299, 3) 0                                            
__________________________________________________________________________________________________
rescaling_1 (Rescaling)         (None, 299, 299, 3)  0           input_2[0][0]                    
__________________________________________________________________________________________________
normalization_1 (Normalization) (None, 299, 299, 3)  7           rescaling_1[0][0]                
__________________________________________________________________________________________________
stem_conv_pad (ZeroPadding2D)   (None, 301, 301, 3)  0           normalization_1[0][0]            
________________________________________________________________________

Instantiate the model.

In [20]:
# Create the ImageCaptioningModel
caption_model = ImageCaptioningModel(
    cnn_model=cnn_model, encoder=encoder, decoder=decoder, image_aug=image_augmentation,
)

# Model testing

Load the desired model weights.

In [21]:
mdx = '231005'  # Sets the version
tmpx = f'/data/Model_weights/{mdx}/Temp/'

# Check for the files
try:
    # Loading weights
    weight_path = f'{tmpx}imgcap_{mdx}'
    fls = os.listdir(tmpx)

    # Look for specific weight files (like .index or .data-00000-of-00001)
    checkpoint_files = [f for f in fls if "imgcap_" in f]
    
    if len(checkpoint_files) > 0:
        print("Found saved weights, loading them now...")
        caption_model.load_weights(weight_path)
        print("Saved weights loaded successfully")
    else:
        print("No saved weights found")
except FileNotFoundError as e:
    print(f"Error: {e}")
except Exception as e:
    print(f"An unexpected error occurred: {e}")


Found saved weights, loading them now...
Saved weights loaded successfully


Function to generate caption.

In [22]:
try:
    vocab = vectorization.get_vocabulary() if vectorization else None
    if vocab:
        index_lookup = dict(zip(range(len(vocab)), vocab))
        print(f"Vocabulary size: {len(vocab)}")
    else:
        index_lookup = None
        print("Vocabulary is missing. Captions may not generate correctly.")
except AttributeError as e:
    index_lookup = None
    print(f"Failed to retrieve vocabulary: {e}")
except Exception as e:
    index_lookup = None
    print(f"Unexpected error while initializing vocabulary: {e}")

max_decoded_sentence_length = SEQ_LENGTH - 1

def generate_caption(caption_model, image_path, display_image=False):
    """
    Generate a caption for the given image.

    Args:
    - caption_model: Trained image captioning model.
    - image_path: Path to the input image.
    - display_image (bool): Whether to display the image. Default is False.

    Returns:
    - str: The generated caption or an error message.
    """
    try:
        # Decode and resize the image
        sample_img = decode_and_resize(image_path)
        print(sample_img)
        if sample_img is None:
            print(f"Error: Image could not be processed for {image_path}.")
            return "Image could not be processed."

        img = sample_img.numpy().clip(0, 255).astype(np.uint8)

        # Display the image if required
        if display_image:
            plt.axis('off')
            plt.imshow(img)
            plt.show()
            plt.close()

        # Process the image
        # Pass the image to the CNN
        img_tensor = tf.expand_dims(sample_img, 0)
        print(f"Image tensor shape: {img_tensor.shape}")
        img_features = caption_model.cnn_model(img_tensor)
        print(f"Features shape after CNN: {img_features.shape}")
        
        # Expand dimensions to make it compatible with the encoder
        img_features = tf.expand_dims(img_features, 1)

        # Encode the image
        # Pass the image features to the Transformer encoder
        encoded_img = caption_model.encoder(img_features, training=False)

        # Decode the caption
        # Generate the caption using the Transformer decoder
        decoded_caption = "<start> "
        for i in range(max_decoded_sentence_length):
            if vectorization is None:
                print("Error: Caption generation unavailable.")
                return "Caption generation unavailable."

            # Ensure decoded_caption is passed as a list of strings
            tokenized_caption = vectorization(tf.constant([decoded_caption]))[:, :-1]
            if tokenized_caption is None or not tf.is_tensor(tokenized_caption):
                print(f"Tokenization failed for caption: {decoded_caption}")
                return "Error: Tokenization failed."
            print(f"Tokenized caption shape: {tokenized_caption.shape}")
            
            # Create mask for the tokenized caption
            mask = tf.math.not_equal(tokenized_caption, 0)
            if mask is None or not tf.is_tensor(mask):
                print("Mask creation failed.")
                return "Error: Mask creation failed."
            print(f"Mask shape: {mask.shape}")
            
            predictions = caption_model.decoder(
                tokenized_caption, encoded_img, training=False, mask=mask
            )
            if predictions is None or not tf.is_tensor(predictions):
                print("Decoder predictions failed.")
                return "Error: Decoder predictions failed."
            print(f"Predictions shape: {predictions.shape}")

            # Get the predicted token
            sampled_token_index = np.argmax(predictions[0, -1, :])

            # Check if token index is valid
            if sampled_token_index >= len(vocab):
                print(f"Warning: Token index {sampled_token_index} out of range.")
                continue
            
            sampled_token = index_lookup[sampled_token_index]
            
            if sampled_token == "[UNK]":
                continue  # Skip unknown tokens

            # Handle noisy or unknown tokens
            if sampled_token in ("[UNK]", ""):
                print(f"Warning: Encountered noisy token '{sampled_token}'. Skipping.")
                continue  # Skip this token

            if sampled_token == "<end>":
                break
            
            decoded_caption += " " + sampled_token

        # Clean the caption
        decoded_caption = (
            decoded_caption.replace("<start> ", "")
            .replace(" <end>", "")
            .replace("[UNK]", "")
            .strip()
        )
        print(f"Generated caption for image {image_path}: {decoded_caption}")
        return decoded_caption
    except Exception as e:
        print(f"Error generating caption for image {image_path}: {e}")
        return "Error generating caption."

Vocabulary size: 3138


Choose the desired images to test.

In [23]:
# Main loop to process test images
dataset_directory = "/data/test/rxxch9vw59-2/"
test_image_filenames = os.listdir(dataset_directory+"images")

# Verify the number of test images
print(f"Number of test images: {len(test_image_filenames)}")

Number of test images: 1442


Display the image and the generated caption.

In [24]:
# Display the image and the generated caption.
captions = {}
for image_name in test_image_filenames[:5]:
    image_path = os.path.join(dataset_directory, "images", image_name)
    caption = generate_caption(caption_model, image_path, display_image=True)
    if caption:
        captions[image_path] = caption
        print(f"Image: {image_name}\nPredicted Caption: {caption}\n")

tf.Tensor(
[[[  5.         13.         16.       ]
  [  5.         13.         16.       ]
  [  5.5267563  13.526756   16.526756 ]
  ...
  [  8.216848   20.216848   32.216846 ]
  [  8.458194   20.458195   32.458195 ]
  [  8.458194   20.458195   32.458195 ]]

 [[  5.6254177  13.625418   16.625418 ]
  [  5.6254177  13.625418   16.625418 ]
  [  5.8227315  13.822731   16.822731 ]
  ...
  [  8.921408   20.921408   32.921406 ]
  [  9.250835   21.250835   33.250835 ]
  [  9.250835   21.250835   33.250835 ]]

 [[  6.         14.         17.       ]
  [  6.         14.         17.       ]
  [  6.         14.         17.       ]
  ...
  [ 10.137707   22.137707   34.137707 ]
  [ 10.29097    22.29097    34.29097  ]
  [ 10.29097    22.29097    34.29097  ]]

 ...

 [[158.42093   142.65898   123.44271  ]
  [153.82774   136.65384   120.270935 ]
  [167.63065   152.48405   136.14848  ]
  ...
  [172.70146   156.42607   132.61723  ]
  [165.04141   144.6434    119.84241  ]
  [204.62683   180.8509    152.98

2024-12-23 03:10:46.714216: I tensorflow/stream_executor/cuda/cuda_dnn.cc:368] Loaded cuDNN version 8401
2024-12-23 03:10:47.854927: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2024-12-23 03:10:47.856346: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2024-12-23 03:10:47.856386: W tensorflow/stream_executor/gpu/asm_compiler.cc:80] Couldn't get ptxas version string: INTERNAL: Couldn't invoke ptxas --version
2024-12-23 03:10:47.857319: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2024-12-23 03:10:47.857399: W tensorflow/stream_executor/gpu/redzone_allocator.cc:314] INTERNAL: Failed to launch ptxas
Relying on driver to perform ptx compilation. 
Modify $PATH to customize ptxas location.
This message will be only logged once.


Features shape after CNN: (1, 256)
Encoder Input Shape: (1, 1, 256)
Encoder Input Shape before LayerNorm: (1, 1, 256)
Encoder Input Shape after LayerNorm: (1, 1, 256)
Encoder Output Shape: (1, 1, 256)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1

In [25]:
# Dictionary to store generated captions
gen_cap = {}

In [26]:
# Save captions to JSON
output_directory = "/results/Captions"
os.makedirs(output_directory, exist_ok=True)  # Ensure the output directory exists

In [27]:
# Generate captions for all images in the dataset
for idx, filename in enumerate(test_image_filenames):
    path = f"{dataset_directory}images/{filename}"
    caption = generate_caption(caption_model, path, display_image=False)
    gen_cap[filename] = caption
    print(f"Processed {idx + 1}/{len(test_image_filenames)}: {filename} -> {caption}")

tf.Tensor(
[[[  5.         13.         16.       ]
  [  5.         13.         16.       ]
  [  5.5267563  13.526756   16.526756 ]
  ...
  [  8.216848   20.216848   32.216846 ]
  [  8.458194   20.458195   32.458195 ]
  [  8.458194   20.458195   32.458195 ]]

 [[  5.6254177  13.625418   16.625418 ]
  [  5.6254177  13.625418   16.625418 ]
  [  5.8227315  13.822731   16.822731 ]
  ...
  [  8.921408   20.921408   32.921406 ]
  [  9.250835   21.250835   33.250835 ]
  [  9.250835   21.250835   33.250835 ]]

 [[  6.         14.         17.       ]
  [  6.         14.         17.       ]
  [  6.         14.         17.       ]
  ...
  [ 10.137707   22.137707   34.137707 ]
  [ 10.29097    22.29097    34.29097  ]
  [ 10.29097    22.29097    34.29097  ]]

 ...

 [[158.42093   142.65898   123.44271  ]
  [153.82774   136.65384   120.270935 ]
  [167.63065   152.48405   136.14848  ]
  ...
  [172.70146   156.42607   132.61723  ]
  [165.04141   144.6434    119.84241  ]
  [204.62683   180.8509    152.98

2024-12-23 03:10:52.059686: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile


tf.Tensor(
[[[37.943142  37.03406   35.03406  ]
  [56.902664  55.902664  53.902664 ]
  [64.23653   60.23653   59.23653  ]
  ...
  [ 1.9027153  1.9027153  1.9027153]
  [ 1.310671   1.310671   1.310671 ]
  [ 2.2380776  2.2380776  2.2380776]]

 [[36.993656  36.7878    34.7878   ]
  [58.189594  57.189594  55.189594 ]
  [69.07358   65.07358   64.07358  ]
  ...
  [ 1.9205163  1.9205163  1.9205163]
  [ 1.9854096  1.9854096  1.9854096]
  [ 1.9148855  1.9148855  1.9148855]]

 [[38.697117  38.626884  36.626884 ]
  [64.63187   63.631863  61.631863 ]
  [70.73442   66.73442   65.73442  ]
  ...
  [ 2.0086935  2.0086935  2.0086935]
  [ 1.         1.         1.       ]
  [ 2.3246777  2.3246777  2.3246777]]

 ...

 [[12.044451  10.044451  11.834295 ]
  [24.707317  23.707317  20.357738 ]
  [28.226036  27.234726  23.375168 ]
  ...
  [ 3.505604   3.505604   3.505604 ]
  [ 2.6237884  2.6237884  2.6237884]
  [ 1.2909546  1.2909546  1.2909546]]

 [[16.731155  16.307913  13.851886 ]
  [21.362497  20.004618  1

2024-12-23 03:10:52.379569: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile


Encoder Input Shape after LayerNorm: (1, 1, 256)
Encoder Output Shape: (1, 1, 256)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape:

...

Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Predictions shape: (1, 7, 3138)
Tokenized caption shape: (1, 7)
Mask shape: (1, 7)
Decoder Input Shape: (1, 7)
Positional Embedding Input Shape: (1, 7)
Positional Embedding Output Shape: (1, 7, 256)
embedded_tokens dtype: <dtype: 'float32'>
embedded_positions dtype: <dtype: 'float32'>
Decoder Output Shape: (1, 7, 3138)
Pr

2024-12-23 03:17:47.228156: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile


tf.Tensor(
[[[249.        248.085     252.82997  ]
  [249.51004   249.51004   251.51004  ]
  [250.        250.        250.96655  ]
  ...
  [  0.         34.         33.       ]
  [  0.         34.         33.       ]
  [  0.         34.         33.       ]]

 [[249.        248.75499   251.49002  ]
  [249.51004   249.51004   251.51004  ]
  [250.        250.        250.96655  ]
  ...
  [  0.         34.         33.       ]
  [  0.         34.         33.       ]
  [  0.         34.         33.       ]]

 [[249.        249.        251.       ]
  [249.9238    249.9238    251.9238   ]
  [250.        250.        251.83928  ]
  ...
  [  0.         34.         33.       ]
  [  0.         34.         33.       ]
  [  0.         34.         33.       ]]

 ...

 [[127.70799   189.92737   190.35349  ]
  [124.77125   183.94371   185.35747  ]
  [129.1752    192.11157   192.43933  ]
  ...
  [ 11.516663   32.516663   33.516663 ]
  [  9.51001    30.51001    31.51001  ]
  [  6.4250245  30.425024   30.42

2024-12-23 03:18:10.000595: W tensorflow/core/lib/png/png_io.cc:88] PNG warning: iCCP: known incorrect sRGB profile


tf.Tensor(
[[[76.75418  72.75418  60.75418 ]
  [76.75418  72.75418  60.75418 ]
  [74.82007  70.82007  58.820072]
  ...
  [58.       54.       45.      ]
  [56.516663 52.516663 43.516663]
  [53.17218  49.17218  40.17218 ]]

 [[80.       76.       64.      ]
  [80.       76.       64.      ]
  [80.226105 76.226105 64.226105]
  ...
  [58.       54.       45.      ]
  [56.516663 52.516663 43.516663]
  [53.17218  49.17218  40.17218 ]]

 [[77.45819  73.45819  61.458195]
  [77.45819  73.45819  61.458195]
  [78.98331  74.98331  62.983303]
  ...
  [58.       54.       45.      ]
  [56.516663 52.516663 43.516663]
  [53.17218  49.17218  40.17218 ]]

 ...

 [[44.39652  51.224277 10.741001]
  [45.864788 51.864788 17.864788]
  [49.1805   53.1805   27.902906]
  ...
  [19.478256 20.339401 16.033676]
  [19.08374  19.08374  19.08374 ]
  [19.08374  19.08374  19.08374 ]]

 [[54.45514  61.282898 20.79962 ]
  [47.973083 53.973083 19.973083]
  [57.31298  61.31298  36.035385]
  ...
  [17.72229  18.583435 14.2

In [28]:
# Save the generated captions to a JSON file
output_file = f"{output_directory}/captions.json"
with open(output_file, "w", encoding="utf-8") as outfile:
    json.dump(gen_cap, outfile, ensure_ascii=False, indent=4)

In [29]:
# Generate captions for specific test cases
# Random image from the test set
random_image = np.random.choice(test_image_filenames)
random_image_path = f"{dataset_directory}images/{random_image}"
print("\nRandom Image Caption:")
generate_caption(caption_model, random_image_path, display_image=True)


Random Image Caption:
tf.Tensor(
[[[ 93.14159   55.53576   36.63048 ]
  [137.33943  100.54367   82.45816 ]
  [149.46815  119.63482  102.687965]
  ...
  [117.84178  151.84178  188.84178 ]
  [137.4588   171.4588   208.4588  ]
  [123.55076  157.55075  194.55075 ]]

 [[100.51919   66.48073   50.49411 ]
  [134.56404  104.24228   86.74597 ]
  [143.06754  116.39922  101.22865 ]
  ...
  [105.74366  139.84901  176.95436 ]
  [109.452515 143.55786  180.66321 ]
  [112.58829  146.69363  183.79898 ]]

 [[169.9792   146.83481  134.28763 ]
  [190.98409  169.56436  156.44229 ]
  [126.92689  108.2001    96.32568 ]
  ...
  [103.71895  138.71895  176.71895 ]
  [103.54364  138.54364  176.54364 ]
  [107.88373  142.88373  180.88373 ]]

 ...

 [[ 38.16083   64.7454    91.93715 ]
  [ 34.130356  61.65715   88.800446]
  [ 33.054672  60.581467  88.60353 ]
  ...
  [ 17.616941  50.327946  79.78784 ]
  [ 19.666641  50.893555  82.169495]
  [ 25.86962   56.23697   90.11452 ]]

 [[ 39.009693  63.7939    89.628494]
  [

'একটি অনেক মানুষ আছে। আছে। ও একটি'

In [30]:
# Caption for the last image in the dataset
last_image_path = f"{dataset_directory}images/{test_image_filenames[-1]}"
print("\nLast Image Caption:")
generate_caption(caption_model, last_image_path, display_image=True)


Last Image Caption:
tf.Tensor(
[[[ 47.         96.        137.       ]
  [ 48.316055   97.316055  138.31606  ]
  [ 49.526756   98.52676   139.52676  ]
  ...
  [  2.5267334   0.5267334   1.5267334]
  [  1.          1.          1.       ]
  [  1.          1.          1.       ]]

 [[ 47.71874    96.71874   137.71873  ]
  [ 48.         97.        138.       ]
  [ 49.20229    98.20229   139.2023   ]
  ...
  [  2.5267334   0.5267334   1.5267334]
  [  1.          1.          1.       ]
  [  1.          1.          1.       ]]

 [[ 48.7241     97.7241    138.7241   ]
  [ 48.         97.        138.       ]
  [ 48.670486   97.67049   138.67049  ]
  ...
  [  2.5267334   0.5267334   1.5267334]
  [  1.          1.          1.       ]
  [  1.          1.          1.       ]]

 ...

 [[ 11.584052   11.584052   13.584052 ]
  [ 14.828167   14.828167   16.828167 ]
  [  8.892918    8.892918   10.892918 ]
  ...
  [ 18.4198     17.4198     22.4198   ]
  [ 20.         19.         24.       ]
  [ 20.     

'একজন বসে কাজ একজন বসে কাজ করছে।'

In [31]:
# Caption for a specific index
specific_index = 8  # Example index, ensure it's within the range
if specific_index < len(test_image_filenames):
    specific_image_path = f"{dataset_directory}images/{test_image_filenames[specific_index]}"
    print(f"\nCaption for Image at Index {specific_index}:")
    generate_caption(caption_model, specific_image_path, display_image=True)
else:
    print(f"Index {specific_index} is out of range for the test dataset.")


Caption for Image at Index 8:
tf.Tensor(
[[[224.65395    215.65395    208.65395   ]
  [231.98117    222.98117    215.98117   ]
  [223.44647    214.44647    207.44647   ]
  ...
  [254.0316     250.75432    247.04155   ]
  [254.54437    248.70796    241.67383   ]
  [246.70575    238.46898    228.57965   ]]

 [[214.52689    205.52689    198.52689   ]
  [230.86845    221.86845    214.86845   ]
  [228.6269     219.6269     213.90115   ]
  ...
  [254.69112    254.17944    251.30489   ]
  [255.         252.30154    246.54446   ]
  [249.55525    244.1033     235.83038   ]]

 [[225.91718    217.04091    210.10278   ]
  [223.84102    214.96475    208.02663   ]
  [225.97913    217.10287    212.041     ]
  ...
  [254.08693    254.05267    253.7024    ]
  [254.37753    253.4573     249.25601   ]
  [250.33418    248.72058    242.5198    ]]

 ...

 [[  0.           0.           0.        ]
  [  0.           0.           0.        ]
  [  0.           0.           0.        ]
  ...
  [  1.           1